In [3]:
from __future__ import print_function, division

from keras.datasets import mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, GlobalAveragePooling2D, MaxPooling2D
from keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import Adam

import matplotlib.pyplot as plt

import numpy as np
from scipy.misc import imread
from scipy.misc import imresize
from scipy.misc import imsave
import glob
import random

from keras.preprocessing.image import ImageDataGenerator
from keras import applications
from keras.optimizers import SGD
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras.callbacks import EarlyStopping
from keras.utils import to_categorical
#from keras.applications.resnet50 import preprocess_input

from keras.applications.resnet50 import ResNet50
from keras.preprocessing import image
from keras.applications.resnet50 import preprocess_input, decode_predictions
#from keras.applications.vgg19 import preprocess_input as preprocess_vgg
from keras.applications.inception_v3 import preprocess_input as inception_preprocess

#from keras.applications.inception_resnet_v2 import preprocess_input

import numpy as np

import keras
import copy
import cv2

from keras.models import *
from keras.layers import *
from keras.optimizers import *

import numpy as np 
import os
import numpy as np
from keras.callbacks import ModelCheckpoint, LearningRateScheduler
from keras import backend as keras

Using TensorFlow backend.


In [4]:
path = '../data/'
savepath = '../data/'
images = glob.glob(path+'new_data/*.npy')

In [5]:
tile_sizes = np.loadtxt(path+'tile_sizes.txt', dtype='int')
images_sampled = {}
for tile in tile_sizes:
    if tile[2] > 200000:
        for i in range(30):
            images_sampled.setdefault(tile[0]*30+i, []).append(tile[1])

In [6]:
def myGenerator(batch_size):
    while True:
        index_list = random.sample(images_sampled.keys(), batch_size)
        alldata_x = []
        alldata_y = []
        for i in index_list:
            frame = path+'sources/new_data/frame'+str(i)+'.npy'
            frame = np.load(frame)
            tile_index = random.choice(images_sampled[i])
            
            temp  = imresize(frame[tile_index], (48, 48))
            temp  = imresize(temp, (384, 384))
            
            alldata_x.append(temp)
            alldata_y.append(frame[tile_index])
        
        alldata_x = np.array(alldata_x)
        alldata_y = np.array(alldata_y)
        
        alldata_y = (alldata_y.astype(np.float32) - 127.5) / 127.5
        alldata_x = alldata_x.astype(np.float32)/255.0
        
        yield alldata_x, alldata_y

#x = myGenerator(10)
#xtrain, ytrain = next(x)
#print('xtrain shape:',xtrain.shape)
#print('ytrain shape:',ytrain.shape)

In [7]:
class CGAN():
    def __init__(self):
        # Input shape
        self.img_rows = 384
        self.img_cols = 384
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminator
        #self.discriminator = self.build_discriminator()
        #self.discriminator.compile(loss=['mse'],
        #    optimizer=optimizer,
        #    metrics=['accuracy'])
        
        #print(self.discriminator.summary())
        
        # Build the generator
        self.generator = self.build_generator()
        
        print(self.generator.summary())
        
        noise = Input(shape=(384, 384, 3))
        img = self.generator(noise)

        # For the combined model we will only train the generator
        #self.discriminator.trainable = False

        # The discriminator takes generated image as input and determines validity
        # and the label of that image
        #valid = self.discriminator(img)
        
        # The combined model  (stacked generator and discriminator)
        # Trains generator to fool discriminator
        #self.combined = Model(noise, [img, valid])
        #self.combined.compile(loss=['mse', 'mse'],
        #    loss_weights=[0.9, 0.1],
        #    optimizer=optimizer)

    def build_generator(self):
        input_size = (384,384,3)
        inputs = Input(input_size)


        conv1 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(inputs)
        conv1 = LeakyReLU()(conv1)
        conv1 = BatchNormalization(momentum=0.8)(conv1)



        conv2 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv1)
        conv2 = LeakyReLU()(conv2)
        conv2 = BatchNormalization(momentum=0.8)(conv2)

        conv3 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv2)
        conv3 = LeakyReLU()(conv3)
        conv3 = BatchNormalization(momentum=0.8)(conv3)

        concat1 = add([conv1, conv3])



        conv4 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(concat1)
        conv4 = LeakyReLU()(conv4)
        conv4 = BatchNormalization(momentum=0.8)(conv4)

        conv5 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv4)
        conv5 = LeakyReLU()(conv5)
        conv5 = BatchNormalization(momentum=0.8)(conv5)

        concat2 = add([conv5, concat1])



        conv6 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(concat2)
        conv6 = LeakyReLU()(conv6)
        conv6 = BatchNormalization(momentum=0.8)(conv6)

        conv7 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv6)
        conv7 = LeakyReLU()(conv7)
        conv7 = BatchNormalization(momentum=0.8)(conv7)

        concat3 = add([conv7, concat2])



        conv8 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(concat3)
        conv8 = LeakyReLU()(conv8)
        conv8 = BatchNormalization(momentum=0.8)(conv8)

        conv9 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv8)
        conv9 = LeakyReLU()(conv9)
        conv9 = BatchNormalization(momentum=0.8)(conv9)
        

        conv10 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv9)
        conv10 = LeakyReLU()(conv10)
        conv10 = BatchNormalization(momentum=0.8)(conv10)

        concat4 = add([conv10, conv1])
        
        conv11 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(concat4)
        conv11 = LeakyReLU()(conv11)
        conv11 = BatchNormalization(momentum=0.8)(conv11)
        
        conv12 = Conv2D(32, 3, padding = 'same', kernel_initializer = 'he_normal')(conv11)
        conv12 = PReLU()(conv12)
        conv12 = BatchNormalization(momentum=0.8)(conv12)


        out = Conv2D(3, 3, padding = 'same', kernel_initializer = 'he_normal')(conv12)
        out = PReLU()(out)
        out = BatchNormalization(momentum=0.8)(out)


        model = Model(input = inputs, output = out)
        return model
    
    def build_autoencoder(self):
        self.generator.compile(loss=['mse'],optimizer=self.optimizer)
    
    def train_generator_autoencoder(self, epochs, batch_size=128, sample_interval=10):
        for epoch in range(epochs):
            X_train, y_train = next(myGenerator(batch_size))
            g_loss = self.generator.train_on_batch(X_train, y_train)
            print ("Epoch ", epoch, " G loss ", g_loss)
            if epoch % sample_interval == 0:
                self.sample_images(epoch)
                self.generator.save_weights(savepath+'weights/generator_weights_'+str(epoch)+'.h5')

    def sample_images(self, epoch):
        r, c             = 1, 10
        X_train, y_train = next(myGenerator(10))
        gen_imgs         = self.generator.predict(X_train)
        
        # Rescale images 0 - 1
        temp     = (0.5 * gen_imgs + 0.5)*255
        gen_imgs = temp.astype(int)
        y_train = (0.5 * y_train + 0.5)*255
        y_train = y_train.astype(int)
        X_train = X_train*255
        X_train = X_train.astype(int)
        
        combined = np.array([gen_imgs[0], gen_imgs[1], gen_imgs[2], gen_imgs[3], gen_imgs[4], gen_imgs[5], gen_imgs[6], gen_imgs[7], gen_imgs[8], gen_imgs[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+".png", combined)
        
        combined = np.array([y_train[0], y_train[1], y_train[2], y_train[3], y_train[4], y_train[5], y_train[6], y_train[7], y_train[8], y_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_real.png", combined)
        
        combined = np.array([X_train[0], X_train[1], X_train[2], X_train[3], X_train[4], X_train[5], X_train[6], X_train[7], X_train[8], X_train[9]])
        combined = np.hstack(combined.reshape(10, 384,384, 3))
        imsave(savepath+"images/"+str(epoch)+"_lowres.png", combined)

In [8]:
cgan = CGAN()
cgan.build_autoencoder()
cgan.train_generator_autoencoder(100000, 6, 100)

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:116: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=Tensor("ba..., inputs=Tensor("in...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 384, 384, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 384, 384, 32) 896         input_1[0][0]                    
__________________________________________________________________________________________________
leaky_re_lu_1 (LeakyReLU)       (None, 384, 384, 32) 0           conv2d_1[0][0]                   
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, 384, 384, 32) 128         leaky_re_lu_1[0][0]              
__________________________________________________________________________________________________
conv2d_2 (

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':


Epoch  0  G loss  0.8430438


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:146: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:150: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:154: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.


...

Epoch  98822  G loss  0.012254379
Epoch  98823  G loss  0.010661821
Epoch  98824  G loss  0.011556979
Epoch  98825  G loss  0.034731656
Epoch  98826  G loss  0.007180099
Epoch  98827  G loss  0.22999705
Epoch  98828  G loss  0.047560398
Epoch  98829  G loss  0.04338625
Epoch  98830  G loss  0.0077810013
Epoch  98831  G loss  0.047623713
Epoch  98832  G loss  0.08351066
Epoch  98833  G loss  0.061034996
Epoch  98834  G loss  0.0070512355
Epoch  98835  G loss  0.03516004
Epoch  98836  G loss  0.022651479
Epoch  98837  G loss  0.019930385
Epoch  98838  G loss  0.005569605
Epoch  98839  G loss  0.011882204
Epoch  98840  G loss  0.011507351
Epoch  98841  G loss  0.19897957
Epoch  98842  G loss  0.010018229
Epoch  98843  G loss  0.0041398196
Epoch  98844  G loss  0.030908177
Epoch  98845  G loss  0.1180309
Epoch  98846  G loss  0.08000407
Epoch  98847  G loss  0.0047989315
Epoch  98848  G loss  0.057504762
Epoch  98849  G loss  0.010324843
Epoch  98850  G loss  0.04341632
Epoch  98851  G los

Epoch  99065  G loss  0.0014939904
Epoch  99066  G loss  0.027444035
Epoch  99067  G loss  0.049127772
Epoch  99068  G loss  0.17907147
Epoch  99069  G loss  0.014110354
Epoch  99070  G loss  0.013849015
Epoch  99071  G loss  0.023892194
Epoch  99072  G loss  0.0036030794
Epoch  99073  G loss  0.03831653
Epoch  99074  G loss  0.01159431
Epoch  99075  G loss  0.0151618095
Epoch  99076  G loss  0.0022458066
Epoch  99077  G loss  0.035470206
Epoch  99078  G loss  0.19957905
Epoch  99079  G loss  0.008672539
Epoch  99080  G loss  0.11164551
Epoch  99081  G loss  0.08386608
Epoch  99082  G loss  0.037191357
Epoch  99083  G loss  0.3466437
Epoch  99084  G loss  0.036853988
Epoch  99085  G loss  0.010468545
Epoch  99086  G loss  0.038759265
Epoch  99087  G loss  0.0021617615
Epoch  99088  G loss  0.015234995
Epoch  99089  G loss  0.02995971
Epoch  99090  G loss  0.004116306
Epoch  99091  G loss  0.053563416
Epoch  99092  G loss  0.06226478
Epoch  99093  G loss  0.008914741
Epoch  99094  G los

Epoch  99307  G loss  0.1074892
Epoch  99308  G loss  0.014075997
Epoch  99309  G loss  0.004094181
Epoch  99310  G loss  0.31787536
Epoch  99311  G loss  0.008088266
Epoch  99312  G loss  0.08448108
Epoch  99313  G loss  0.01885631
Epoch  99314  G loss  0.075265095
Epoch  99315  G loss  0.025820943
Epoch  99316  G loss  0.002940487
Epoch  99317  G loss  0.09439056
Epoch  99318  G loss  0.04031739
Epoch  99319  G loss  0.034000676
Epoch  99320  G loss  0.03944175
Epoch  99321  G loss  0.0222751
Epoch  99322  G loss  0.017613148
Epoch  99323  G loss  0.017523661
Epoch  99324  G loss  0.09607621
Epoch  99325  G loss  0.035019156
Epoch  99326  G loss  0.03434972
Epoch  99327  G loss  0.08457821
Epoch  99328  G loss  0.0024698123
Epoch  99329  G loss  0.011047523
Epoch  99330  G loss  0.014200769
Epoch  99331  G loss  0.0066556516
Epoch  99332  G loss  0.023327572
Epoch  99333  G loss  0.04577117
Epoch  99334  G loss  0.0315264
Epoch  99335  G loss  0.0073781065
Epoch  99336  G loss  0.089

Epoch  99551  G loss  0.04008075
Epoch  99552  G loss  0.06283966
Epoch  99553  G loss  0.03257667
Epoch  99554  G loss  0.031061405
Epoch  99555  G loss  0.035582278
Epoch  99556  G loss  0.0114193605
Epoch  99557  G loss  0.017085599
Epoch  99558  G loss  0.060069147
Epoch  99559  G loss  0.06996711
Epoch  99560  G loss  0.016373323
Epoch  99561  G loss  0.07998411
Epoch  99562  G loss  0.0107441135
Epoch  99563  G loss  0.008788869
Epoch  99564  G loss  0.0057512964
Epoch  99565  G loss  0.01765423
Epoch  99566  G loss  0.020545384
Epoch  99567  G loss  0.06742249
Epoch  99568  G loss  0.05958358
Epoch  99569  G loss  0.09378142
Epoch  99570  G loss  0.0049031866
Epoch  99571  G loss  0.01515633
Epoch  99572  G loss  0.008928488
Epoch  99573  G loss  0.0054757334
Epoch  99574  G loss  0.007622972
Epoch  99575  G loss  0.094699375
Epoch  99576  G loss  0.0026210963
Epoch  99577  G loss  0.07517371
Epoch  99578  G loss  0.026070127
Epoch  99579  G loss  0.029528193
Epoch  99580  G los

Epoch  99794  G loss  0.004715678
Epoch  99795  G loss  0.09064197
Epoch  99796  G loss  0.01824628
Epoch  99797  G loss  0.0069640465
Epoch  99798  G loss  0.07835764
Epoch  99799  G loss  0.027042734
Epoch  99800  G loss  0.038009044
Epoch  99801  G loss  0.021871569
Epoch  99802  G loss  0.035048697
Epoch  99803  G loss  0.01603281
Epoch  99804  G loss  0.0059317467
Epoch  99805  G loss  0.0068903845
Epoch  99806  G loss  0.0936521
Epoch  99807  G loss  0.2417369
Epoch  99808  G loss  0.018423982
Epoch  99809  G loss  0.10882152
Epoch  99810  G loss  0.029209143
Epoch  99811  G loss  0.010137385
Epoch  99812  G loss  0.06438451
Epoch  99813  G loss  0.080566026
Epoch  99814  G loss  0.13421099
Epoch  99815  G loss  0.060997557
Epoch  99816  G loss  0.007917536
Epoch  99817  G loss  0.026570609
Epoch  99818  G loss  0.03020104
Epoch  99819  G loss  0.10740515
Epoch  99820  G loss  0.029781714
Epoch  99821  G loss  0.013868213
Epoch  99822  G loss  0.14156692
Epoch  99823  G loss  0.0

In [31]:
for i in range(1000):
    x = myGenerator(1)
    xtest, ytest = next(x)
    pred = cgan.generator.predict(xtest)
    pred = pred*127.5 + 127.5
    pred = pred.astype(int)
    #plt.imshow(pred[0])
    #plt.show()
    ytest = ytest*127.5+127.5
    ytest = ytest.astype(int)
    #plt.imshow(ytest[0])
    #plt.show()
    imsave(path+'test/frame_pred'+str(i)+'.png', pred[0])
    imsave(path+'test/frame_real'+str(i)+'.png', ytest[0])

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:12: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
  if sys.path[0] == '':
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:13: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  del sys.path[0]
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:14: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  


In [32]:
import numpy 
import math
import cv2

def psnr(img1, img2):
    mse = numpy.mean( (img1 - img2) ** 2 )
    if mse == 0:
        return 100
    PIXEL_MAX = 255.0
    return 20 * math.log10(PIXEL_MAX / math.sqrt(mse))

In [36]:
data = []
for i in range(1000):
    img1 = cv2.imread(path+'test/frame_real'+str(i)+'.png')
    img2 = cv2.imread(path+'test/frame_pred'+str(i)+'.png')
    d = psnr(img1, img2)
    data.append(d)
print('PSNR:', np.mean(data))

PSNR: 31.612699630864867
